# Recommender System with Scipy linalg svds SVD Model (Option 2)

### Elizabeth Hanley
### Uniqname: hanleyel
### Kaggle ID: hanleyel

In [1]:
import pandas as pd
import json
import gzip
import numpy as np
import scipy
from scipy.sparse import csr_matrix
from scipy.sparse import csc_matrix
from scipy.sparse.linalg import svds
import sklearn
from sklearn.neighbors import NearestNeighbors
from sklearn.preprocessing import normalize
import csv
from sparsesvd import sparsesvd
import math
import operator
import random

In [2]:
# Unzips gzip data.
def unzip_json(filename):
    
    print('Unzipping json file...')
    
    unzipped_data = pd.read_json(gzip.open(filename), lines=True)
    
    return unzipped_data

In [3]:
unzip_json('reviews.training.json.gz')

In [4]:
# Outputs json training data as a Pandas dataframe.
def json_to_df(file_name):

    print('Converting json file to dataframe...')

    try:
        training_data = pd.read_json(file_name, lines=True)
        return training_data
    except:
        print('Please try another file name.')

        return None

In [5]:
training_df = json_to_df('reviews.training.json')

Converting json file to dataframe...


In [6]:
# dev_df = json_to_df('reviews.dev.json')

In [7]:
# Converts dataframe to csv.
def convert_to_csv(dataframe, desired_filename):

    print('Converting dataframe to csv: ' + desired_filename + '...')

    try:
        return dataframe.to_csv(desired_filename, index=False)
    except:
        print('Please try another dataframe or file name.')

    return None

In [8]:
# Training file to CSV
convert_to_csv(training_df[['reviewerID', 'asin', 'overall']].head(25000), 'reviews.training.shortened.csv')

Converting dataframe to csv: reviews.training.shortened.csv...


In [9]:
# Development file to CSV.
# convert_to_csv(dev_df[['reviewerID', 'asin', 'overall']], 'reviews.dev.csv')

In [10]:
# Returns dictionaries with unique users and products as keys and unique ints as values.
def create_user_product_dicts(filename):

    print('Creating dictionaries from CSV for unique users and products...')

    user_dict = {}
    product_dict = {}
    user_count = 0
    product_count = 0

    with open(filename, 'r') as train_file:
        file_reader=csv.reader(train_file, delimiter=',')
        next(file_reader, None)

        for row in file_reader:
            if row[0] not in user_dict:
                user_dict[row[0]] = user_count
                user_count += 1
            if row[1] not in product_dict:
                product_dict[row[1]] = product_count
                product_count += 1

    return user_dict, product_dict, user_count, product_count

In [11]:
user_dict, product_dict, user_count, product_count = create_user_product_dicts('reviews.training.shortened.csv')

Creating dictionaries from CSV for unique users and products...


In [12]:
# Creates a dense matrix from training data.
def training_mtx(filename, user_dict, product_dict):

        print('Creating a dense matrix from training data...')

        num_user_ids = len(user_dict)
        num_product_ids = len(product_dict)

        dense_matrix = np.zeros(shape=(num_user_ids, num_product_ids), dtype=np.float32)

        with open(filename, 'r') as train_file:
            matrix_reader = csv.reader(train_file, delimiter=',')
            next(matrix_reader, None)
            for row in matrix_reader:
                dense_matrix[user_dict[row[0]], product_dict[row[1]]] = float(row[2])

        return dense_matrix

In [13]:
training_matrix = training_mtx('reviews.training.shortened.csv', user_dict, product_dict)

Creating a dense matrix from training data...


In [14]:
training_matrix

array([[4., 0., 0., ..., 0., 0., 0.],
       [0., 5., 0., ..., 0., 0., 0.],
       [0., 0., 5., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 5., 0.],
       [0., 0., 0., ..., 0., 0., 5.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)

In [15]:
training_matrix.shape

(18380, 13554)

In [16]:
# Outputs dictionaries with unique test users and test products.
def get_test_users_products(filename, training_user_dict, training_product_dict):

    print('Importing test users and products...')

    test_user_count = len(training_user_dict)
    test_product_count = len(training_product_dict)
    test_user_dict = training_user_dict.copy()
    test_product_dict = training_product_dict.copy()

    with open(filename, 'r') as test_file:
        test_reader = csv.reader(test_file, delimiter=',')
        next(test_reader, None)

        for row in test_reader:
            # Add unique users to test_user dictionary.
            if row[1] not in test_user_dict:
                test_user_dict[row[1]] = test_user_count
                test_user_count += 1
            # Add unique products to test_product dictionary.
            # print(row[2])
            if row[2] not in test_product_dict:
                test_product_dict[row[2]] = test_product_count
                test_product_count += 1

    return test_user_dict, test_product_dict

In [17]:
test_user_dict, test_product_dict = get_test_users_products('reviews.test.unlabeled.csv', user_dict, product_dict)

Importing test users and products...


In [18]:
# Creates a new matrix with unknown products on the x axis.
def merged_mtx_products(filename, user_dict, test_product_dict):
    
        print('Creating a matrix with new products on the x axis...')

        num_user_ids = len(user_dict)
        num_product_ids = len(test_product_dict)

        dense_matrix = np.zeros(shape=(num_user_ids, num_product_ids), dtype=np.float32)

        with open(filename, 'r') as train_file:
            matrix_reader = csv.reader(train_file, delimiter=',')
            next(matrix_reader, None)
            for row in matrix_reader:
                dense_matrix[user_dict[row[0]], product_dict[row[1]]] = float(row[2])

        return dense_matrix

In [19]:
merged_matrix_product_rows = merged_mtx_products('reviews.training.shortened.csv', user_dict, test_product_dict)

Creating a matrix with new products on the x axis...


In [20]:
merged_matrix_product_rows.shape

(18380, 39171)

In [21]:
merged_matrix_product_rows

array([[4., 0., 0., ..., 0., 0., 0.],
       [0., 5., 0., ..., 0., 0., 0.],
       [0., 0., 5., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)

In [22]:
sum(merged_matrix_product_rows[-1,:])

5.0

In [23]:
# Creates a new matrix with unknown products on the y axis.
def merged_mtx_users(filename, product_dict, test_user_dict):

        print('Creating a matrix with new users on the x axis...')

        num_product_ids = len(product_dict)
        num_user_ids = len(test_user_dict)

        dense_matrix = np.zeros(shape=(num_product_ids, num_user_ids), dtype=np.float32)

        with open(filename, 'r') as train_file:
            matrix_reader = csv.reader(train_file, delimiter=',')
            next(matrix_reader, None)
            for row in matrix_reader:
                dense_matrix[product_dict[row[1]], user_dict[row[0]]] = float(row[2])

        return dense_matrix

In [24]:
merged_matrix_user_rows = merged_mtx_users('reviews.training.shortened.csv', product_dict, test_user_dict)

Creating a matrix with new users on the x axis...


In [25]:
merged_matrix_user_rows.shape

(13554, 78725)

In [26]:
merged_matrix_user_rows

array([[4., 0., 0., ..., 0., 0., 0.],
       [0., 5., 0., ..., 0., 0., 0.],
       [0., 0., 5., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)

In [27]:
sum(merged_matrix_user_rows[-1, :])

5.0

In [28]:
# Converts dense matrices to sparse.
def to_sparse(filename_prefix, matrix):
    print('Creating a sparse matrix...')
    try:
        # Try loading previously saved sparse matrix from file (becaues I keep crashing my kernel)
        loader = np.load(filename_prefix + '.npz')
        sparse_matrix = csr_matrix((loader['data'], loader['indices'], loader['indptr']), shape=loader['shape'], dtype=np.float32)
        loader.close()
    except:
        # Create sparse matrix from dense matrix, write to file as backup
        sparse_matrix = scipy.sparse.csr_matrix(matrix, dtype=np.float32)
        scipy.sparse.save_npz((filename_prefix + 'npz'), sparse_matrix)
    return sparse_matrix

In [29]:
sparse_merged_matrix_pr = to_sparse('sparse.merged.matrix.pr', merged_matrix_product_rows)

Creating a sparse matrix...


In [30]:
sparse_merged_matrix_pr.dtype

dtype('float32')

In [31]:
sparse_merged_matrix_pr.shape

(18380, 39171)

In [32]:
sparse_merged_matrix_ur = to_sparse('sparse.merged.matrix.ur', merged_matrix_user_rows)

Creating a sparse matrix...


In [33]:
sparse_merged_matrix_ur.shape

(13554, 78725)

In [34]:
# Normalizes matrix.
def normalize_merged_matrix(sparse_matrix, dense_merged_matrix):

    print('Calculating global mean...')
    global_mean = sparse_matrix.sum()/(sparse_matrix != 0).sum()
    print(global_mean)
    
    print('Calculating row mean...')
    matrix_row_mean = sparse_matrix.sum(1)/(sparse_matrix != 0).sum(1)
    print(matrix_row_mean)

    print('Normalizing the data...')
    normalized_matrix = sparse_matrix.copy()
    normalized_matrix -= matrix_row_mean.reshape(-1, 1)
    
    print('Normalized matrix: ')
    print(normalized_matrix.shape)
    print(normalized_matrix)

    return normalized_matrix, matrix_row_mean, global_mean

In [35]:
normalized_matrix_products, matrix_row_mean_products, global_mean = normalize_merged_matrix(sparse_merged_matrix_pr,
                                                                                            merged_matrix_product_rows)

Calculating global mean...
4.10176
Calculating row mean...
[[4.]
 [4.]
 [5.]
 ...
 [5.]
 [5.]
 [5.]]
Normalizing the data...
Normalized matrix: 
(18380, 39171)
[[ 0. -4. -4. ... -4. -4. -4.]
 [-4.  1. -4. ... -4. -4. -4.]
 [-5. -5.  0. ... -5. -5. -5.]
 ...
 [-5. -5. -5. ... -5. -5. -5.]
 [-5. -5. -5. ... -5. -5. -5.]
 [-5. -5. -5. ... -5. -5. -5.]]


In [36]:
normalized_matrix_users, matrix_row_mean_users, global_mean = normalize_merged_matrix(sparse_merged_matrix_ur,
                                                                                     merged_matrix_user_rows)

Calculating global mean...
4.10176
Calculating row mean...
[[4.2]
 [4.5]
 [5. ]
 ...
 [5. ]
 [5. ]
 [5. ]]
Normalizing the data...
Normalized matrix: 
(13554, 78725)
[[-0.2 -4.2 -4.2 ... -4.2 -4.2 -4.2]
 [-4.5  0.5 -4.5 ... -4.5 -4.5 -4.5]
 [-5.  -5.   0.  ... -5.  -5.  -5. ]
 ...
 [-5.  -5.  -5.  ... -5.  -5.  -5. ]
 [-5.  -5.  -5.  ... -5.  -5.  -5. ]
 [-5.  -5.  -5.  ... -5.  -5.  -5. ]]


In [37]:
# Implements an SVD model.
def compute_svd_from_normalized(normalized_matrix):

    print('Computing svd from de-meaned matrix...')

    U, sigma, Vt = svds(normalized_matrix, k = 100)
    S = np.diag(sigma)

    return U, S, Vt

In [38]:
U_products, S_products, Vt_products = compute_svd_from_normalized(merged_matrix_product_rows)

Computing svd from de-meaned matrix...


In [39]:
predictions_product_rows = np.dot(np.dot(U_products, S_products), Vt_products)-normalized_matrix_products

In [40]:
predictions_product_rows

matrix([[ 1.63067639e+00,  3.99994590e+00,  4.00000000e+00, ...,
          4.00000000e+00,  4.00000000e+00,  4.00000000e+00],
        [ 3.99991602e+00, -2.10610271e-01,  4.00000000e+00, ...,
          4.00000000e+00,  4.00000000e+00,  4.00000000e+00],
        [ 4.99999999e+00,  5.00000000e+00,  9.02471677e-16, ...,
          5.00000000e+00,  5.00000000e+00,  5.00000000e+00],
        ...,
        [ 5.00000001e+00,  5.00000000e+00,  5.00000000e+00, ...,
          5.00000000e+00,  5.00000000e+00,  5.00000000e+00],
        [ 5.00000000e+00,  5.00000000e+00,  5.00000000e+00, ...,
          5.00000000e+00,  5.00000000e+00,  5.00000000e+00],
        [ 4.99999716e+00,  4.99999952e+00,  5.00000000e+00, ...,
          5.00000000e+00,  5.00000000e+00,  5.00000000e+00]])

In [41]:
predictions_product_rows.shape

(18380, 39171)

In [42]:
U_users, S_users, Vt_users = compute_svd_from_normalized(merged_matrix_user_rows)

Computing svd from de-meaned matrix...


In [43]:
predictions_user_rows = np.dot(np.dot(U_users, S_users), Vt_users)-normalized_matrix_users

In [44]:
predictions_user_rows

matrix([[1.83075066e+00, 4.19991623e+00, 4.20000000e+00, ...,
         4.20000000e+00, 4.20000000e+00, 4.20000000e+00],
        [4.49994599e+00, 2.89390683e-01, 4.50000000e+00, ...,
         4.50000000e+00, 4.50000000e+00, 4.50000000e+00],
        [5.00000000e+00, 5.00000000e+00, 2.15472956e-17, ...,
         5.00000000e+00, 5.00000000e+00, 5.00000000e+00],
        ...,
        [5.00000000e+00, 5.00000000e+00, 5.00000000e+00, ...,
         5.00000000e+00, 5.00000000e+00, 5.00000000e+00],
        [5.00000000e+00, 5.00000000e+00, 5.00000000e+00, ...,
         5.00000000e+00, 5.00000000e+00, 5.00000000e+00],
        [5.00000000e+00, 5.00000000e+00, 5.00000000e+00, ...,
         5.00000000e+00, 5.00000000e+00, 5.00000000e+00]])

In [45]:
merged_prediction_matrix = np.zeros(shape=(len(test_user_dict), len(test_product_dict)))

In [46]:
merged_prediction_matrix.shape

(78725, 39171)

In [59]:
# Queries the prediction matrix.
def query_normalized_matrix_test(test_file, prediction_file, test_user_dict, test_product_dict,
                                predictions_product_rows, predictions_user_rows, global_mean):

    print('Reconstructing matrix and making predictions...')

    with open(test_file, 'r') as test_file:
        test_reader = csv.reader(test_file, delimiter=',')
        next(test_reader, None)
        with open(prediction_file, 'w') as outfile:
            outfile_reader = csv.writer(outfile, delimiter=',')
            outfile_reader.writerow(['datapointID', 'overall'])
            


            for row in test_reader:
                prediction = random.randrange(1,5,1)

                try:
                    # Query by user (new products on x axis).
                    user_query = predictions_product_rows[user_dict[row[1]]]
                    prediction = user_query[0, test_product_dict[row[2]]]
                    outfile_reader.writerow([row[0], prediction])
                    # print('Query by USER')
                    # print(prediction)
                except:
                    try:
                        # Query by product.
                        product_query = predictions_user_rows[product_dict[row[2]]]
                        prediction = product_query[0, test_user_dict[row[1]]]
                        outfile_reader.writerow([row[0], prediction])
                        # print('Query by PRODUCT')
                        # print(prediction)
                    except:
                        # If no matching users or products are found, make prediction based on global mean.
                        prediction = global_mean
                        outfile_reader.writerow([row[0], prediction])
                        # print('No matching query: GLOBAL MEAN')
                        # print(prediction)

    print('Done.')
    return None

In [60]:
predicted_ratings = query_normalized_matrix_test('reviews.test.unlabeled.csv', 'reviews.test.labeled.csv',
                                                test_user_dict, test_product_dict, predictions_product_rows,
                                                predictions_user_rows, global_mean)

Reconstructing matrix and making predictions...
Query by USER
5.0
Query by USER
3.700079509452917
Query by PRODUCT
2.3333333333333335
Query by PRODUCT
5.0
Query by USER
5.0
No matching query: GLOBAL MEAN
4.10176
Query by USER
5.0
Query by PRODUCT
4.666666666666667
Query by PRODUCT
4.333333333333333
Query by PRODUCT
2.5
Query by PRODUCT
5.0
Query by PRODUCT
4.0
Query by USER
5.0
No matching query: GLOBAL MEAN
4.10176
Query by PRODUCT
5.0
Query by PRODUCT
4.5
Query by USER
5.0
Query by USER
3.890335139249348
Query by PRODUCT
3.625
Query by PRODUCT
4.0
Query by PRODUCT
4.0
No matching query: GLOBAL MEAN
4.10176
Query by USER
4.000000000039013
No matching query: GLOBAL MEAN
4.10176
Query by PRODUCT
5.0
Query by USER
4.2
Query by USER
4.999999999116963
Query by PRODUCT
4.166666666666667
No matching query: GLOBAL MEAN
4.10176
No matching query: GLOBAL MEAN
4.10176
No matching query: GLOBAL MEAN
4.10176
No matching query: GLOBAL MEAN
4.10176
Query by PRODUCT
4.75
Query by PRODUCT
4.75
Query b

3.5
Query by USER
5.0
Query by USER
3.49999994915121
Query by USER
4.5
Query by USER
3.99999999988538
No matching query: GLOBAL MEAN
4.10176
Query by PRODUCT
2.142857142857143
Query by PRODUCT
4.333333333333333
Query by PRODUCT
4.375
Query by USER
1.5
Query by PRODUCT
5.0
Query by PRODUCT
4.125
No matching query: GLOBAL MEAN
4.10176
Query by USER
4.0
Query by USER
5.0
No matching query: GLOBAL MEAN
4.10176
Query by USER
3.5995798923191615
Query by PRODUCT
4.0
No matching query: GLOBAL MEAN
4.10176
No matching query: GLOBAL MEAN
4.10176
Query by USER
4.499999999947967
No matching query: GLOBAL MEAN
4.10176
Query by PRODUCT
2.0
Query by PRODUCT
4.0
Query by PRODUCT
4.25
No matching query: GLOBAL MEAN
4.10176
Query by PRODUCT
4.4
Query by USER
3.0
Query by USER
5.0
No matching query: GLOBAL MEAN
4.10176
Query by PRODUCT
4.0
Query by USER
5.0
No matching query: GLOBAL MEAN
4.10176
No matching query: GLOBAL MEAN
4.10176
No matching query: GLOBAL MEAN
4.10176
Query by USER
4.99999999841891
N

4.10176
No matching query: GLOBAL MEAN
4.10176
Query by USER
5.000419004703872
Query by PRODUCT
3.625
Query by USER
4.999999999946264
No matching query: GLOBAL MEAN
4.10176
Query by USER
2.499913508800091
Query by USER
3.8749999984001837
Query by PRODUCT
5.0
No matching query: GLOBAL MEAN
4.10176
Query by PRODUCT
4.333333333333333
Query by USER
3.6000000004447696
Query by PRODUCT
5.0
No matching query: GLOBAL MEAN
4.10176
No matching query: GLOBAL MEAN
4.10176
No matching query: GLOBAL MEAN
4.10176
Query by PRODUCT
3.5
No matching query: GLOBAL MEAN
4.10176
Query by PRODUCT
4.0
Query by USER
4.125000000004173
Query by USER
3.0000000000799263
Query by PRODUCT
4.583333333333333
Query by PRODUCT
3.8333333333333335
Query by USER
4.500001484595032
Query by PRODUCT
5.0
Query by USER
3.9999887857266003
Query by PRODUCT
4.0
Query by PRODUCT
3.6666666666666665
Query by USER
4.249638266861439
Query by USER
4.222222217065085
Query by PRODUCT
3.3333333333333335
No matching query: GLOBAL MEAN
4.101

Query by PRODUCT
4.75
Query by PRODUCT
3.0
No matching query: GLOBAL MEAN
4.10176
Query by PRODUCT
5.0
Query by USER
4.142857083765606
Query by USER
3.0000000000056137
Query by PRODUCT
4.407407407407407
Query by PRODUCT
5.0
No matching query: GLOBAL MEAN
4.10176
No matching query: GLOBAL MEAN
4.10176
Query by PRODUCT
4.75
Query by USER
4.0
Query by PRODUCT
4.0
No matching query: GLOBAL MEAN
4.10176
No matching query: GLOBAL MEAN
4.10176
No matching query: GLOBAL MEAN
4.10176
Query by USER
5.0
No matching query: GLOBAL MEAN
4.10176
Query by USER
4.394753791508552
Query by USER
5.0
Query by USER
3.75
Query by PRODUCT
5.0
Query by PRODUCT
5.0
Query by PRODUCT
5.0
Query by PRODUCT
3.0
Query by PRODUCT
4.0
Query by USER
4.999999999828999
Query by USER
5.0
Query by PRODUCT
4.444444444444445
Query by USER
4.000000000065545
Query by PRODUCT
4.782608695652174
Query by PRODUCT
5.0
Query by USER
4.999999997068531
Query by PRODUCT
4.666666666666667
Query by PRODUCT
5.0
No matching query: GLOBAL ME

Query by USER
5.0
Query by USER
5.0
Query by USER
3.0
Query by PRODUCT
2.0
Query by USER
3.0
Query by USER
5.0000000001229274
No matching query: GLOBAL MEAN
4.10176
Query by PRODUCT
3.875
Query by USER
4.1111111130436
Query by PRODUCT
3.0
Query by PRODUCT
4.0
Query by PRODUCT
3.0
No matching query: GLOBAL MEAN
4.10176
Query by USER
4.666226823853019
Query by USER
4.0
Query by USER
3.9999928732941044
Query by USER
5.000000000250543
Query by USER
3.9999999940428292
Query by USER
5.0
Query by USER
4.027862875340765
Query by USER
3.7777552398151277
Query by USER
3.857369279588706
Query by USER
3.6666666666666665
Query by USER
3.496214092709124
No matching query: GLOBAL MEAN
4.10176
No matching query: GLOBAL MEAN
4.10176
Query by USER
5.000000009904802
No matching query: GLOBAL MEAN
4.10176
Query by PRODUCT
5.0
Query by PRODUCT
3.0
No matching query: GLOBAL MEAN
4.10176
No matching query: GLOBAL MEAN
4.10176
Query by PRODUCT
5.0
Query by USER
5.0
Query by USER
3.9999999983150034
Query by PR

...

5.0
Query by PRODUCT
5.0
Query by PRODUCT
5.0
No matching query: GLOBAL MEAN
4.10176
Query by PRODUCT
4.571428571428571
No matching query: GLOBAL MEAN
4.10176
No matching query: GLOBAL MEAN
4.10176
Query by USER
4.999999999920187
Query by USER
3.9998142429394647
Query by USER
5.000000000371252
Query by USER
3.364121219714765
Query by USER
2.253360621863976
No matching query: GLOBAL MEAN
4.10176
No matching query: GLOBAL MEAN
4.10176
Query by USER
4.000000000001491
No matching query: GLOBAL MEAN
4.10176
No matching query: GLOBAL MEAN
4.10176
Query by PRODUCT
5.0
Query by USER
1.0
No matching query: GLOBAL MEAN
4.10176
Query by USER
4.0
Query by USER
3.7999999999998697
Query by PRODUCT
4.0
Query by PRODUCT
3.4285714285714284
No matching query: GLOBAL MEAN
4.10176
Query by USER
4.999999999999549
Query by PRODUCT
4.333333333333333
No matching query: GLOBAL MEAN
4.10176
Query by USER
3.0
Query by PRODUCT
3.0
Query by USER
3.0
Query by USER
4.6
Query by PRODUCT
4.333333333333333
Query by USE

Query by PRODUCT
5.0
Query by USER
4.499999999951887
Query by PRODUCT
4.0
Query by USER
2.0
Query by PRODUCT
5.0
No matching query: GLOBAL MEAN
4.10176
Query by PRODUCT
3.5
No matching query: GLOBAL MEAN
4.10176
Query by PRODUCT
5.0
No matching query: GLOBAL MEAN
4.10176
No matching query: GLOBAL MEAN
4.10176
No matching query: GLOBAL MEAN
4.10176
No matching query: GLOBAL MEAN
4.10176
Query by PRODUCT
3.2142857142857144
Query by USER
5.0
Query by USER
3.75
Query by USER
3.7999999998505585
Query by USER
4.000464983051643
Query by PRODUCT
3.466666666666667
Query by PRODUCT
4.0
Query by PRODUCT
4.0
Query by PRODUCT
4.25
Query by PRODUCT
5.0
No matching query: GLOBAL MEAN
4.10176
Query by USER
3.4999998570067277
Query by PRODUCT
4.0
Query by PRODUCT
5.0
Query by PRODUCT
4.333333333333333
No matching query: GLOBAL MEAN
4.10176
Query by USER
3.0
Query by PRODUCT
4.666666666666667
Query by USER
4.0
Query by PRODUCT
4.428571428571429
Query by USER
4.999984801164828
Query by PRODUCT
5.0
Query 

Query by USER
4.0
Query by USER
5.000000047799933
Query by USER
2.925925925925926
Query by USER
4.2
Query by USER
5.0000000089980166
Query by PRODUCT
3.6666666666666665
No matching query: GLOBAL MEAN
4.10176
Query by USER
1.0
Query by USER
3.4999999828780233
No matching query: GLOBAL MEAN
4.10176
Query by USER
3.9999920544396446
Query by PRODUCT
4.0
Query by USER
3.818586105486082
No matching query: GLOBAL MEAN
4.10176
Query by PRODUCT
5.0
Query by PRODUCT
4.5
Query by USER
4.499999999276467
Query by USER
5.0
Query by PRODUCT
4.666666666666667
Query by PRODUCT
4.538461538461538
No matching query: GLOBAL MEAN
4.10176
Query by USER
2.5999947149808578
Query by PRODUCT
4.0
Query by USER
3.2857142857142856
Query by PRODUCT
5.0
Query by USER
4.0
Query by PRODUCT
5.0
No matching query: GLOBAL MEAN
4.10176
Query by PRODUCT
4.0
Query by USER
5.0
Query by PRODUCT
5.0
Query by USER
4.818181818181818
Query by PRODUCT
4.0
No matching query: GLOBAL MEAN
4.10176
Query by USER
5.000000000011444
Query 

4.10176
Query by USER
4.799988381505318
Query by USER
0.9999999999999971
Query by PRODUCT
4.333333333333333
Query by PRODUCT
5.0
Query by PRODUCT
4.5
Query by USER
3.9166666662704124
Query by USER
5.0
Query by PRODUCT
5.0
Query by USER
4.000000004250795
Query by USER
5.000000000007565
No matching query: GLOBAL MEAN
4.10176
Query by PRODUCT
4.75
Query by PRODUCT
1.5
Query by USER
3.5
Query by PRODUCT
4.5
Query by USER
5.0
Query by USER
3.6666666666666665
Query by USER
3.0000000000000018
Query by USER
3.891378511571222
Query by USER
4.000000001727186
Query by USER
2.9999999999149876
Query by USER
4.0
Query by USER
5.0
Query by PRODUCT
4.8
Query by USER
3.6666666666666665
Query by PRODUCT
5.0
Query by PRODUCT
4.607142857142857
No matching query: GLOBAL MEAN
4.10176
Query by USER
5.0
Query by USER
4.000000000113174
Query by PRODUCT
3.0
Query by PRODUCT
3.4285714285714284
Query by PRODUCT
4.666666666666667
Query by USER
3.8192453938007187
Query by USER
1.9999999994878732
Query by PRODUCT
5.

Query by PRODUCT
3.6666666666666665
No matching query: GLOBAL MEAN
4.10176
Query by PRODUCT
2.3333333333333335
Query by USER
5.0
Query by USER
4.0
Query by USER
4.666666666666667
Query by USER
0.9999999999106044
Query by PRODUCT
5.0
Query by PRODUCT
5.0
Query by USER
5.0
Query by PRODUCT
5.0
Query by PRODUCT
3.0
Query by PRODUCT
4.363636363636363
Query by USER
4.312499999886537
Query by USER
4.999999999980461
Query by USER
3.25
No matching query: GLOBAL MEAN
4.10176
No matching query: GLOBAL MEAN
4.10176
No matching query: GLOBAL MEAN
4.10176
Query by USER
4.000010461444617
Query by PRODUCT
4.5
No matching query: GLOBAL MEAN
4.10176
No matching query: GLOBAL MEAN
4.10176
Query by PRODUCT
5.0
Query by USER
3.000000000043197
Query by USER
5.000000000058915
Query by USER
5.0
Query by USER
3.0000000000311644
Query by USER
2.0
Query by USER
4.99889334035106
Query by PRODUCT
5.0
Query by USER
4.0
Query by PRODUCT
4.2
Query by USER
4.500033675041777
Query by PRODUCT
5.0
Query by USER
3.666668

In [61]:
# RMSE analysis
def rmse(analysis_file):
    
    print('Checking RMSE...')
    
    targets = np.array([])
    predictions = np.array([])

    with open(analysis_file, 'r') as analysis_file:
        analysis_reader = csv.reader(analysis_file, delimiter=',')
        next(analysis_reader, None)
        for row in analysis_reader:
                targets = np.append(targets, row[1])
                predictions = np.append(predictions, row[2])

    return np.sqrt(((predictions - targets) ** 2).mean())

In [62]:
# rmse_val = rmse('reviews.dev.labeled.2.csv')
# print("rms error is: " + str(rmse_val))

In [ ]:
import pandas as pd
import json
import gzip
import numpy as np
import scipy
from scipy.sparse import csr_matrix
from scipy.sparse import csc_matrix
from scipy.sparse.linalg import svds
import sklearn
from sklearn.neighbors import NearestNeighbors
from sklearn.preprocessing import normalize
import csv
from sparsesvd import sparsesvd
import math
import operator
import random
import decimal

In [ ]:
# Unzips gzip data.
def unzip_json(filename):
    
    print('Unzipping json file...')
    
    unzipped_data = pd.read_json(gzip.open(filename), lines=True)
    
    return unzipped_data

In [ ]:
unzip_json('reviews.training.json.gz')

In [ ]:
# Outputs json training data as a Pandas dataframe.
def json_to_df(file_name):

    print('Converting json file to dataframe...')

    try:
        training_data = pd.read_json(file_name, lines=True)
        return training_data
    except:
        print('Please try another file name.')

        return None

In [ ]:
training_df = json_to_df('reviews.training.json')

In [ ]:
# dev_df = json_to_df('reviews.dev.json')

In [ ]:
# Converts dataframe to csv.
def convert_to_csv(dataframe, desired_filename):

    print('Converting dataframe to csv: ' + desired_filename + '...')

    try:
        return dataframe.to_csv(desired_filename, index=False)
    except:
        print('Please try another dataframe or file name.')

    return None

In [ ]:
# Training file to CSV
convert_to_csv(training_df[['reviewerID', 'asin', 'overall']].head(90000), 'reviews.training.shortened.csv')

In [ ]:
# Development file to CSV.
# convert_to_csv(dev_df[['reviewerID', 'asin', 'overall']], 'reviews.dev.csv')

In [ ]:
# Returns dictionaries with unique users and products as keys and unique ints as values.
def create_user_product_dicts(filename):

    print('Creating dictionaries from CSV for unique users and products...')

    user_dict = {}
    product_dict = {}
    user_count = 0
    product_count = 0

    with open(filename, 'r') as train_file:
        file_reader=csv.reader(train_file, delimiter=',')
        next(file_reader, None)

        for row in file_reader:
            if row[0] not in user_dict:
                user_dict[row[0]] = user_count
                user_count += 1
            if row[1] not in product_dict:
                product_dict[row[1]] = product_count
                product_count += 1

    return user_dict, product_dict, user_count, product_count

In [ ]:
user_dict, product_dict, user_count, product_count = create_user_product_dicts('reviews.training.shortened.csv')

In [ ]:
# Creates a dense matrix from training data.
def training_mtx(filename, user_dict, product_dict):

        print('Creating a dense matrix from training data...')

        num_user_ids = len(user_dict)
        num_product_ids = len(product_dict)

        dense_matrix = np.zeros(shape=(num_user_ids, num_product_ids), dtype=np.float32)

        with open(filename, 'r') as train_file:
            matrix_reader = csv.reader(train_file, delimiter=',')
            next(matrix_reader, None)
            for row in matrix_reader:
                dense_matrix[user_dict[row[0]], product_dict[row[1]]] = float(row[2])

        return dense_matrix

In [ ]:
training_matrix = training_mtx('reviews.training.shortened.csv', user_dict, product_dict)

In [ ]:
training_matrix

In [ ]:
# Outputs dictionaries with unique test users and test products.
def get_test_users_products(filename, training_user_dict, training_product_dict):

    print('Importing test users and products...')

    test_user_count = len(training_user_dict)
    test_product_count = len(training_product_dict)
    test_user_dict = training_user_dict.copy()
    test_product_dict = training_product_dict.copy()

    with open(filename, 'r') as test_file:
        test_reader = csv.reader(test_file, delimiter=',')
        next(test_reader, None)

        for row in test_reader:
            # Add unique users to test_user dictionary.
            if row[0] not in test_user_dict:
                test_user_dict[row[0]] = test_user_count
                test_user_count += 1
            # Add unique products to test_product dictionary.
            # print(row[2])
            if row[1] not in test_product_dict:
                test_product_dict[row[1]] = test_product_count
                test_product_count += 1

    return test_user_dict, test_product_dict

In [ ]:
test_user_dict, test_product_dict = get_test_users_products('reviews.dev.csv', user_dict, product_dict)

In [ ]:
# Converts dense matrices to sparse.
def to_sparse(filename_prefix, matrix):
    print('Creating a sparse matrix...')
    try:
        # Try loading previously saved sparse matrix from file (becaues I keep crashing my kernel)
        loader = np.load(filename_prefix + '.npz')
        sparse_matrix = csr_matrix((loader['data'], loader['indices'], loader['indptr']), shape=loader['shape'], dtype=np.float32)
        loader.close()
    except:
        # Create sparse matrix from dense matrix, write to file as backup
        sparse_matrix = scipy.sparse.csr_matrix(matrix, dtype=np.float32)
        scipy.sparse.save_npz((filename_prefix + 'npz'), sparse_matrix)
    return sparse_matrix

In [ ]:
sparse_matrix = to_sparse('merged.matrix', training_matrix)

In [1]:
# Calculate global, row, and column means
def calculate_means(sparse_matrix):
    print('Calculating global mean...')
    # global_mean = sparse_matrix.sum()/(sparse_matrix != 0).sum()
    global_mean = np.true_divide(sparse_matrix.sum(), (sparse_matrix != 0).sum(), dtype=np.float32)
    print(global_mean)
    
    print('Calculating row mean...')
    matrix_row_mean = np.true_divide(sparse_matrix.sum(1), (sparse_matrix != 0).sum(1), dtype=np.float32)
    print(matrix_row_mean[-1])
    
    np.savetxt("row.mean.csv", matrix_row_mean, delimiter=",")
    
#     row_pad_len = len(test_user_dict) - len(user_dict)
#     matrix_row_mean_padded = np.pad(matrix_row_mean, (0, row_pad_len), 'constant')
#     print(matrix_row_mean_padded)
    
    
    print('Calculating column mean...')
    matrix_column_mean = np.true_divide(sparse_matrix.sum(0), (sparse_matrix != 0).sum(0), dtype=np.float32)
    print(matrix_column_mean)
    
    np.savetxt("column.mean.csv", matrix_column_mean.T, delimiter=",")

    return global_mean, matrix_row_mean, matrix_column_mean

In [ ]:
global_mean, matrix_row_mean, matrix_column_mean = calculate_means(sparse_matrix)

In [ ]:
# Merge test data and normalize matrix.
def normalize_matrix(sparse_matrix, global_mean, matrix_row_mean, matrix_column_mean):
    
    print('Creating a new matrix for merging test data scores...')

    num_product_ids = len(test_product_dict)
    num_user_ids = len(test_user_dict)

    dense_merged_matrix = np.full((num_user_ids+1, num_product_ids+1), 0, dtype=np.float32)
    
    
    with open('row.mean.csv', 'r') as infile:
        file_reader = csv.reader(infile, delimiter=',')
        row_count = 0
        for row in file_reader:
            dense_merged_matrix[row_count, :] = (float(row[0])-global_mean)/2
            row_count += 1
            
    print(dense_merged_matrix)
            
    with open('column.mean.csv', 'r') as infile:
        file_reader = csv.reader(infile, delimiter=',')
        column_count = 0
        for row in file_reader:
            dense_merged_matrix[:, column_count] += (float(row[0])-global_mean)/2
            column_count += 1

#     print('Normalizing the data...')
#     normalized_matrix = np.add(merged_matrix, matrix_row_mean_padded)
    
#     print('Normalized matrix: ')
#     print(normalized_matrix.shape)
#     print(normalized_matrix)

    return dense_merged_matrix

In [ ]:
normalized_matrix = normalize_matrix(sparse_matrix, global_mean, matrix_row_mean, matrix_column_mean)

In [ ]:
# Implements an SVD model.
def compute_svd_from_normalized(normalized_matrix):

    print('Computing svd from de-meaned matrix...')

    U, sigma, Vt = svds(normalized_matrix, k = 100)
    # U, sigma, Vt = np.linalg.svd(normalized_matrix)
    S = np.diag(sigma)

    return U, S, Vt

In [ ]:
U, S, Vt = compute_svd_from_normalized(normalized_matrix.astype(float))

In [ ]:
normalized_predictions = np.dot(np.dot(U, S), Vt)

In [ ]:
predictions_matrix = normalized_predictions+global_mean

In [ ]:
def query_matrix(infile, outfile, predictions_matrix):
    
    print(predictions_matrix.shape)
    
    with open(infile, 'r') as test_file:
        test_reader = csv.reader(test_file, delimiter=',')
        next(test_reader, None)
        with open(outfile, 'w') as outfile:
            outfile_reader = csv.writer(outfile, delimiter=',')
            outfile_reader.writerow(['datapointID', 'overall'])

            for row in test_reader:
                
                try:
                    prediction = predictions_matrix[test_user_dict[row[0]], test_product_dict[row[1]]]
                    outfile_reader.writerow([row[0], row[2], prediction])
                    print(row[2], prediction)
                except:
                    print('Error')
                    pass
    
    return None

In [ ]:
query_matrix('reviews.dev.csv', 'reviews.test.labeled.csv', predictions_matrix)

In [ ]:
# RMSE analysis
def rmse(analysis_file):
    
    print('Checking RMSE...')
    
    targets = np.array([])
    predictions = np.array([])

    with open(analysis_file, 'r') as analysis_file:
        analysis_reader = csv.reader(analysis_file, delimiter=',')
        next(analysis_reader, None)
        for row in analysis_reader:
                targets = np.append(targets, row[1])
                predictions = np.append(predictions, row[2])

    return np.sqrt(((predictions - targets) ** 2).mean())

In [ ]:
# rmse_val = rmse('reviews.dev.labeled.2.csv')
# print("rms error is: " + str(rmse_val))